# Import Libraries

In [1]:
import pandas as pd
import numpy as np
import pandas_profiling as pp
from pycaret.classification import *

# Variables to Set

In [2]:
data_file = 'classification_dataset.csv'
target_column = 'Survived'

# Load/Transform Data

In [37]:
df = pd.read_csv(data_file)
df[target_column] = df[target_column].astype(object)
df.head()

PassengerId Survived  Pclass  \
0            1        0       3   
1            2        1       1   
2            3        1       3   
3            4        1       1   
4            5        0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

# Feature Engineering

In [45]:
age_bin_labels = [ 'Child', 'Young', 'Middle', 'Elderly']
df['Age_Bin_Label'] = pd.qcut(df['Age'],
                              q=4,
                              labels=age_bin_labels)

df['Dr'] = np.where(df['Name'].str.contains('Dr. '),1,0)
df['Age_Impute'] = df['Age'].fillna(df.groupby('Sex')['Age'].transform('mean'))
df['Fare_Max'] = np.where(df['Fare']>=45,45,df['Fare'])
df.head()

PassengerId Survived  Pclass  \
0            1        0       3   
1            2        1       1   
2            3        1       3   
3            4        1       1   
4            5        0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked Age_Bin_Label  Dr  \
0      0         A/5 21171   7.2500   NaN        S         Young   0   
1      0          PC 17599  71.2833   C85        C        Middle   0   
2      0  STON/O2. 3101282   7.9250   NaN        S         Young   0   
3      0            113803  53.1000  C123        S        Middle   0   
4      0            373450   8.0500   NaN        S        Middle   0   

   Age_Impute  Fare_Max  
0        22.0     7.250  
1        38.0    45.000  
2        26.0     7.925  
3        35.0    45.000  
4        35.0     8.050

In [46]:
df.dtypes

PassengerId         int64
Survived           object
Pclass              int64
Name               object
Sex                object
Age               float64
SibSp               int64
Parch               int64
Ticket             object
Fare              float64
Cabin              object
Embarked           object
Age_Bin_Label    category
Dr                  int32
Age_Impute        float64
Fare_Max          float64
dtype: object

# Profile Data

In [47]:
pp.ProfileReport(df)

# Split into Training/Test and Validation Data

In [48]:
data = df.sample(frac=0.75, random_state=786)
data_unseen = df.drop(data.index)

data.reset_index(drop=True, inplace=True)
data_unseen.reset_index(drop=True, inplace=True)

print('Data for Modeling: ' + str(data.shape))
print('Unseen Data For Predictions: ' + str(data_unseen.shape))

Data for Modeling: (668, 16)
Unseen Data For Predictions: (223, 16)


# Setup Dataset with Pycaret

In [49]:
cla = setup(data = data, 
            target = target_column , 
            session_id=123,
            silent = True,
            verbose = True) 

# Compare Classification Models

In [50]:
compare_models(
#         include = ['']
#         exclude = ['']
)

GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                           learning_rate=0.1, loss='deviance', max_depth=3,
                           max_features=None, max_leaf_nodes=None,
                           min_impurity_decrease=0.0, min_impurity_split=None,
                           min_samples_leaf=1, min_samples_split=2,
                           min_weight_fraction_leaf=0.0, n_estimators=100,
                           n_iter_no_change=None, presort='deprecated',
                           random_state=123, subsample=1.0, tol=0.0001,
                           validation_fraction=0.1, verbose=0,
                           warm_start=False)

# Build a Logistic Regression Model

In [51]:
lr = create_model('lr')

# Tune Logistic Regression Model

In [52]:
tuned_lr = tune_model(lr)

In [53]:
print(tuned_lr)

LogisticRegression(C=6.718000000000001, class_weight={}, dual=False,
                   fit_intercept=True, intercept_scaling=1, l1_ratio=None,
                   max_iter=1000, multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=123, solver='lbfgs', tol=0.0001, verbose=0,
                   warm_start=False)


# Evaluate Logistic Regression Model

In [54]:
evaluate_model(lr)

Parameters
C                        1.0
class_weight            None
dual                   False
fit_intercept           True
intercept_scaling          1
l1_ratio                None
max_iter                1000
multi_class             auto
n_jobs                  None
penalty                   l2
random_state             123
solver                 lbfgs
tol                   0.0001
verbose                    0
warm_start             False

# Predict on Test Dataset

In [55]:
predict_model(tuned_lr)

PassengerId       Fare  Dr  Age_Impute   Fare_Max  Pclass_1  Pclass_2  \
0          395.0  16.700001   0   24.000000  16.700001       0.0       0.0   
1          231.0  83.474998   0   35.000000  45.000000       1.0       0.0   
2          542.0  31.275000   0    9.000000  31.275000       0.0       0.0   
3          131.0   7.895800   0   33.000000   7.895800       0.0       0.0   
4          239.0  10.500000   0   19.000000  10.500000       0.0       1.0   
..           ...        ...  ..         ...        ...       ...       ...   
196        688.0  10.170800   0   19.000000  10.170800       0.0       0.0   
197        719.0  15.500000   0   30.726645  15.500000       0.0       0.0   
198        110.0  24.150000   0   27.915709  24.150000       0.0       0.0   
199          3.0   7.925000   0   26.000000   7.925000       0.0       0.0   
200        136.0  15.045800   0   23.000000  15.045800       0.0       1.0   

     Pclass_3  Name_Abelson Mrs. Samuel (Hannah Wizosky)  \
0         1.0                                        0.0   
1         0.0                                        0.0   
2         1.0                                        0.0   
3         1.0                                        0.0   
4         0.0                                        0.0   
..        ...                                        ...   
196       1.0                                        0.0   
197       1.0                                        0.0   
198       1.0                                        0.0   
199       1.0                                        0.0   
200       0.0                                        0.0   

     Name_Aks Mrs. Sam (Leah Rosen)  ...  Embarked_Q  Embarked_S  \
0                               0.0  ...         0.0         1.0   
1                               0.0  ...         0.0         1.0   
2                               0.0  ...         0.0         1.0   
3                               0.0  ...         0.0         0.0   
4                               0.0  ...         0.0         1.0   
..                              ...  ...         ...         ...   
196                             0.0  ...         0.0         1.0   
197                             0.0  ...         1.0         0.0   
198                             0.0  ...         1.0         0.0   
199                             0.0  ...         0.0         1.0   
200                             0.0  ...         0.0         0.0   

     Age_Bin_Label_Child  Age_Bin_Label_Elderly  Age_Bin_Label_Middle  \
0                    0.0                    0.0                   0.0   
1                    0.0                    0.0                   1.0   
2                    1.0                    0.0                   0.0   
3                    0.0                    0.0                   1.0   
4                    1.0                    0.0                   0.0   
..                   ...                    ...                   ...   
196                  1.0                    0.0                   0.0   
197                  0.0                    0.0                   0.0   
198                  0.0                    0.0                   0.0   
199                  0.0                    0.0                   0.0   
200                  0.0                    0.0                   0.0   

     Age_Bin_Label_Young  Age_Bin_Label_not_available  Survived  Label   Score  
0                    1.0                          0.0         1      1  0.5866  
1                    0.0                          0.0         1      1  0.9789  
2                    0.0                          0.0         0      0  0.6618  
3                    0.0                          0.0         0      0  0.6011  
4                    0.0                          0.0         0      1  0.5780  
..                   ...                          ...       ...    ...     ...  
196                  0.0                          0.0         0      0  0.6544  
197  

# Predict on Validation Data

In [56]:
unseen_predictions = predict_model(tuned_lr, data=data_unseen)
unseen_predictions

PassengerId Survived  Pclass  \
0              4        1       1   
1              6        0       3   
2              8        0       3   
3             12        1       1   
4             14        0       3   
..           ...      ...     ...   
218          876        1       3   
219          877        0       3   
220          880        1       1   
221          883        0       3   
222          887        0       2   

                                              Name     Sex   Age  SibSp  \
0     Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
1                                 Moran, Mr. James    male   NaN      0   
2                   Palsson, Master. Gosta Leonard    male   2.0      3   
3                         Bonnell, Miss. Elizabeth  female  58.0      0   
4                      Andersson, Mr. Anders Johan    male  39.0      1   
..                                             ...     ...   ...    ...   
218               Najib, Miss. Adele Kiamie "Jane"  female  15.0      0   
219                  Gustafsson, Mr. Alfred Ossian    male  20.0      0   
220  Potter, Mrs. Thomas Jr (Lily Alexenia Wilson)  female  56.0      0   
221                   Dahlberg, Miss. Gerda Ulrika  female  22.0      0   
222                          Montvila, Rev. Juozas    male  27.0      0   

     Parch  Ticket     Fare Cabin Embarked Age_Bin_Label  Dr  Age_Impute  \
0        0  113803  53.1000  C123        S        Middle   0   35.000000   
1        0  330877   8.4583   NaN        Q           NaN   0   30.726645   
2        1  349909  21.0750   NaN        S         Child   0    2.000000   
3        0  113783  26.5500  C103        S       Elderly   0   58.000000   
4        5  347082  31.2750   NaN        S       Elderly   0   39.000000   
..     ...     ...      ...   ...      ...           ...  ..         ...   
218      0    2667   7.2250   NaN        C         Child   0   15.000000   
219      0    7534   9.8458   NaN        S         Child   0   20.000000   
220      1   11767  83.1583   C50        C       Elderly   0   56.000000   
221      0    7552  10.5167   NaN        S         Young   0   22.000000   
222      0  211536  13.0000   NaN        S         Young   0   27.000000   

     Fare_Max  Label   Score  
0     45.0000      1  0.9937  
1      8.4583      0  0.7783  
2     21.0750      0  0.9874  
3     26.5500      1  0.9488  
4     31.2750      0  0.9839  
..        ...    ...     ...  
218    7.2250      1  0.9933  
219    9.8458      0  0.6417  
220   45.0000      1  0.9918  
221   10.5167      1  0.9453  
222   13.0000      0  0.5969  

[223 rows x 18 columns]

In [57]:
from pycaret.utils import check_metric
check_metric(unseen_predictions[target_column], unseen_predictions.Label, 'AUC')

0.7788

# Predict on Kaggle Titanic Data

In [58]:
kaggle_test = pd.read_csv('classification_dataset_validation.csv')
kaggle_predictions = predict_model(tuned_lr, data=kaggle_test)
kaggle_predictions

KeyError: "['Fare_Max', 'Age_Bin_Label', 'Dr', 'Age_Impute'] not in index"